
## Title translation and similarity comparison (training)<br>

In the following, and we translate the titles using Google Translate API (find documentation at [googletrans 4.0.0rc1](https://pypi.org/project/googletrans/4.0.0rc1/) ). After that, we embed them using a pre-trained language model (**BERT**) and apply **cosine similarity** to give a first human readable score of title similarity.


### Important remarks on Google Translate API

As can be read in the documentation, this API has several critical restriction for its use which we list below: <br><br>

1. The maximum character limit for translation of a single text is 15k  
2. The number of files that can be translated in a single session is highly variable. In our experience, it is between 1 and 5000 files. 
3. The API can easily ban the user's client IP address for a variable time (several hours usually) as a consequence of a great usage of the service. This might also depend on how many translations are done per unit of time, this means that sometimes the execution of programs has been artificially stopped or delayed (e.g. with `time.sleep()`).
4. The API depends on the status and stability of the web version of Google Translate

In [3]:
import os
from bs4 import BeautifulSoup
import json
from googletrans import Translator # pip install googletrans==4.0.0-rc1
# import fasttext # pip install fastText
import pandas as pd
import numpy as np

from sklearn.metrics.pairwise import cosine_similarity
from sentence_transformers import SentenceTransformer

translator = Translator()
model = SentenceTransformer('bert-base-nli-mean-tokens')

In [5]:
train_df = pd.read_csv ('train/_TRAIN_details_in_df.csv')
train_df

pair_id url1_lang url2_lang  \
0     1484084337_1484110209        en        en   
1     1484396422_1483924666        en        en   
2     1484698254_1483758694        en        en   
3     1576314516_1576455088        en        en   
4     1484036253_1483894099        en        en   
...                     ...       ...       ...   
4959  1586195445_1598778991        tr        tr   
4960  1590915424_1590940388        tr        tr   
4961  1526157103_1492737005        tr        tr   
4962  1603274500_1618292937        tr        tr   
4963  1597247537_1604202164        tr        tr   

                                                 title1  \
0     Virginia man arrested in fatal DUI crash in We...   
1     Guyana: Three injured after car crashes into u...   
2     Trump Brings In 2020 At Mar-a-Lago: ‘We’re Goi...   
3     Zomato Buys Uber’s Food Delivery Business in I...   
4     India approves third moon mission, months afte...   
...                                                 ...   
4959  BM, Aden'de 2 bini aşkın iç göçmenin selden za...   
4960  Kovid-19'dan dolayı La Liga kulüplerinde hayat...   
4961  Saray da çare olmadı: 'Borca boğulan dev kulüp...   
4962  Ergene Belediyesi yol çalışmalarına aksatmadan...   
4963  Grup Yorum üyeleri zorla başlatmıştı... İbrahi...   

                                                 title2  \
0     Haiti’s leader marks independence day amid sec...   
1     Fire kills more than 30 animals at zoo in west...   
2     Trump says he does not expect war with Iran, ‘...   
3     Indian Online Food Delivery Market to Hit $8 B...   
4                India targets new moon mission in 2020   
...                                                 ...   
4959  BM'den Yemen'de kadınların doğumda ölüm riski ...   
4960  Fabio Capello: Koronavirüs sonrası La Liga'da ...   
4961    TFF’den jet yanıt! ''Bizi hedef gösteriyorlar''   
4962  Ergene'de Ahimehmet ve Yeşiltepe mahallelerind...   
4963  Savcılık Karşıyaka Hakimi Sarısu'nun DHKP-C sa...   

                                              keywords1  \
0     law and order,reckless endangerment,transporta...   
1                                                   NaN   
2                                                   NaN   
3     zomatoubereatsbusinessacquisitionindiaallstock...   
4                 india,lunarorbiter,isro,landonthemoon   
...                                                 ...   
4959  twitter,yemen,güncel,birleşmişmilletler,birleş...   
4960  laliga,la liga,i̇spanya,spor,futbol,realmadrid...   
4961  satiş,'borca,olmadi:,kulüpler,çare,da,masasınd...   
4962  tekirdağ,ergene,rasimyüksel,güncel,koronavirüs...   
4963  hdp,dhkp c,grup yorum,son dakika,grupyorum,can...   

                                              keywords2  \
0     port au prince,latinamericaandcaribbean,jean,c...   
1                       smg2_world,smg_europe,smg2_news   
2     full coverage 2020 us presidential elections,f...   
3     swiggy,ber,indian online food delivery market ...   
4                                           india,space   
...                                                 ...   
4959  haber,yemen,güncel,birleşmişmilletler,birleşmi...   
4960  kovid 19,i̇spanya1futbolligi,la liga,laliga,ko...   
4961  tff,ahmet nur çebi,türkiye futbol federasyonu,...   
4962                  yeşiltepe,yaşam,koronavirüs,haber   
4963  ayşe sarısu pehlivan,dhkp c,gazimahallesi,terö...   

                                                  text1  \
0     MARTINSBURG, W.Va. — A suspected drunken drive...   
1     Share This On:\n\nPin 11 Shares\n\n(NEWS ROOM ...   
2     (Breitbart) – President Donald Trump welcomed ...   
3     Uber has sold its online food-ordering busines...   
4     BENGALURU (Reuters) - India has approved its t...   
...                                                 ...   
4959  BM, Aden'de 2 bini aşkın iç göçmenin selden za...   
4960  Kovid-19'dan dolayı La Liga kulüplerinde hayat...   
4961  \n\n\n\n\n\n\n\nİflas noktasındaki


### Title translation

In what follows, we translate to English the title entries that are in a different language. Then, we compare the annotated language `url1_lang` and `url2_lang` with the languages detected by the automatic *source language* function of the Google Translate API (`.src`). <br><br>

The limitations of the Google Translate API have been avoided by dividing the titles into batches.

In [14]:
title_df = pd.DataFrame(columns = ["pair_id","url1_lang", "google_lang1","url2_lang","google_lang2", "title1","title2"])


In [15]:
i = 0
j = i+5000
(start,finish) = (i,j)

for index, row in train_df.iterrows():  
    if index < i:
        continue
    
    #we had to handle the file with title "Wyborcza.pl" individually
    if pd.isnull(row["title1"]) or row["title1"]=='Wyborcza.pl':
        translated1 = ' '
        lang1 = row["url1_lang"]
    elif row["url1_lang"] == 'en':
        translated1 =  row['title1']
        lang1 = row['url1_lang']
    else:
        result1 = translator.translate(row["title1"])
        translated1 =  result1.text
        lang1 = result1.src
        
    if pd.isnull(row["title2"]) or row["title2"]=='Wyborcza.pl':
        translated2 = ' '
        lang2 = row["url2_lang"]
    elif row["url2_lang"] == 'en':
        translated2 =  row['title2']
        lang2 = row['url2_lang']
    else:
        result2 = translator.translate(row["title2"])
        translated2 =  result2.text
        lang2 = result2.src
    
    
    
    print('---------------------',index,'-----------------------')
    print(row['pair_id'])
    print(row['title1'])
    print(row['url1_lang'],' ; ',lang1)
    print(translated1)
    print(row['title2'])
    print(row['url2_lang'],' ; ',lang2)
    print(translated2)
        
    entry = {"pair_id":row['pair_id'],"url1_lang":row['url1_lang'],"google_lang1":lang1,"url2_lang":row['url2_lang'],"google_lang2":lang2,"title1":row["title1"],"title2":row["title2"],"translated1":translated1,"translated2":translated2}
    title_df = title_df.append(entry, ignore_index = True)
    


--------------------- 0 -----------------------
1484084337_1484110209
Virginia man arrested in fatal DUI crash in West Virginia
en  ;  en
Virginia man arrested in fatal DUI crash in West Virginia
Haiti’s leader marks independence day amid security concerns
en  ;  en
Haiti’s leader marks independence day amid security concerns
--------------------- 1 -----------------------
1484396422_1483924666
Guyana: Three injured after car crashes into utility pole
en  ;  en
Guyana: Three injured after car crashes into utility pole
Fire kills more than 30 animals at zoo in western Germany
en  ;  en
Fire kills more than 30 animals at zoo in western Germany
--------------------- 2 -----------------------
1484698254_1483758694
Trump Brings In 2020 At Mar-a-Lago: ‘We’re Going To Have A Great Year’
en  ;  en
Trump Brings In 2020 At Mar-a-Lago: ‘We’re Going To Have A Great Year’
Trump says he does not expect war with Iran, ‘likes peace’
en  ;  en
Trump says he does not expect war with Iran, ‘likes peace’


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\4002546768.py:44: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_df = title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\4002546768.py:44: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_df = title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\4002546768.py:44: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_df = title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\4002546768.py:44: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_df = titl

 7 -----------------------
1484188439_1484378177
The biggest business con of 2019: fleecing workers while bosses get rich
en  ;  en
The biggest business con of 2019: fleecing workers while bosses get rich
The left’s constant victimhood olympics is a gift to anti-Semites
en  ;  en
The left’s constant victimhood olympics is a gift to anti-Semites
--------------------- 8 -----------------------
1484011751_1483920335
The Compatriots: The Brutal and Chaotic History of Russia's Exiles, Émigrés, and Agents Abroad: Soldatov, Andrei, Borogan, Irina: 9781541730168: Amazon.com: Books
en  ;  en
The Compatriots: The Brutal and Chaotic History of Russia's Exiles, Émigrés, and Agents Abroad: Soldatov, Andrei, Borogan, Irina: 9781541730168: Amazon.com: Books
The Red Web: The Kremlin's Wars on the Internet: Soldatov, Andrei, Borogan, Irina: 9781610399579: Amazon.com: Books
en  ;  en
The Red Web: The Kremlin's Wars on the Internet: Soldatov, Andrei, Borogan, Irina: 9781610399579: Amazon.com: Books
-----

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\4002546768.py:44: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_df = title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\4002546768.py:44: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_df = title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\4002546768.py:44: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_df = title_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\4002546768.py:44: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_df = titl

en
MIAA
--------------------- 15 -----------------------
1484702073_1484760850
2020 Declared Year of Artificial Intelligence in Telangana as Govt Signs MoUs with Cos, IITs
en  ;  en
2020 Declared Year of Artificial Intelligence in Telangana as Govt Signs MoUs with Cos, IITs
'It Warmed My Heart': Sachin Tendulkar Rings in New Year With an Inspirational Message on Twitter
en  ;  en
'It Warmed My Heart': Sachin Tendulkar Rings in New Year With an Inspirational Message on Twitter
--------------------- 16 -----------------------
1484084344_1484110209
MD Lottery
en  ;  en
MD Lottery
Haiti’s leader marks independence day amid security concerns
en  ;  en
Haiti’s leader marks independence day amid security concerns
--------------------- 17 -----------------------
1484033615_1483970348
TMC observes foundation day as ‘Citizens’ Day’, vows to continue protests till CAA is withdrawn
en  ;  en
TMC observes foundation day as ‘Citizens’ Day’, vows to continue protests till CAA is withdrawn
Actor Swara

...

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\4002546768.py:44: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_df = title_df.append(entry, ignore_index = True)


--------------------- 4962 -----------------------
1603274500_1618292937
Ergene Belediyesi yol çalışmalarına aksatmadan devam ediyor
tr  ;  tr
Ergene Municipality continues to disrupt road work
Ergene'de Ahimehmet ve Yeşiltepe mahallelerinde maske dağıtıldı
tr  ;  tr
Mask was distributed in Ahimehmet and Yeşiltepe neighborhoods in Ergene


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\4002546768.py:44: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_df = title_df.append(entry, ignore_index = True)


--------------------- 4963 -----------------------
1597247537_1604202164
Grup Yorum üyeleri zorla başlatmıştı... İbrahim Gökçek ölüm orucunu bıraktı!
tr  ;  tr
The group had launched members of the comment members ... Ibrahim Gökçek left the death of death!
Savcılık Karşıyaka Hakimi Sarısu'nun DHKP-C sanığı hakkındaki paylaşımları nedeniyle harekete geçti
tr  ;  tr
Prosecutor's Carsitaki Judge Yarsu has been moving due to shares on DHKP-C defendant


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\4002546768.py:44: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_df = title_df.append(entry, ignore_index = True)


In [16]:
title_df

pair_id url1_lang google_lang1 url2_lang google_lang2  \
0     1484084337_1484110209        en           en        en           en   
1     1484396422_1483924666        en           en        en           en   
2     1484698254_1483758694        en           en        en           en   
3     1576314516_1576455088        en           en        en           en   
4     1484036253_1483894099        en           en        en           en   
...                     ...       ...          ...       ...          ...   
4959  1586195445_1598778991        tr           tr        tr           tr   
4960  1590915424_1590940388        tr           tr        tr           tr   
4961  1526157103_1492737005        tr           tr        tr           tr   
4962  1603274500_1618292937        tr           tr        tr           tr   
4963  1597247537_1604202164        tr           tr        tr           tr   

                                                 title1  \
0     Virginia man arrested in fatal DUI crash in We...   
1     Guyana: Three injured after car crashes into u...   
2     Trump Brings In 2020 At Mar-a-Lago: ‘We’re Goi...   
3     Zomato Buys Uber’s Food Delivery Business in I...   
4     India approves third moon mission, months afte...   
...                                                 ...   
4959  BM, Aden'de 2 bini aşkın iç göçmenin selden za...   
4960  Kovid-19'dan dolayı La Liga kulüplerinde hayat...   
4961  Saray da çare olmadı: 'Borca boğulan dev kulüp...   
4962  Ergene Belediyesi yol çalışmalarına aksatmadan...   
4963  Grup Yorum üyeleri zorla başlatmıştı... İbrahi...   

                                                 title2  \
0     Haiti’s leader marks independence day amid sec...   
1     Fire kills more than 30 animals at zoo in west...   
2     Trump says he does not expect war with Iran, ‘...   
3     Indian Online Food Delivery Market to Hit $8 B...   
4                India targets new moon mission in 2020   
...                                                 ...   
4959  BM'den Yemen'de kadınların doğumda ölüm riski ...   
4960  Fabio Capello: Koronavirüs sonrası La Liga'da ...   
4961    TFF’den jet yanıt! ''Bizi hedef gösteriyorlar''   
4962  Ergene'de Ahimehmet ve Yeşiltepe mahallelerind...   
4963  Savcılık Karşıyaka Hakimi Sarısu'nun DHKP-C sa...   

                                            translated1  \
0     Virginia man arrested in fatal DUI crash in We...   
1     Guyana: Three injured after car crashes into u...   
2     Trump Brings In 2020 At Mar-a-Lago: ‘We’re Goi...   
3     Zomato Buys Uber’s Food Delivery Business in I...   
4     India approves third moon mission, months afte...   
...                                                 ...   
4959  UN explained that over 2,000 domestic migrants...   
4960  Survival Struggle in La Liga Clubs due to Kovi...   
4961  The palace has not been the remedy: 'Giant Clu...   
4962  Ergene Municipality continues to disrupt road ...   
4963  The group had launched members of the comment ...   

                                            translated2  
0     Haiti’s leader marks independence day amid sec...  
1     Fire kills more than 30 animals at zoo in west...  
2     Trump says he does not expect war with Iran, ‘...  
3     Indian Online Food Delivery Market to Hit $8 B...  
4                India targets new moon mission in 2020  
...                                                 ...  
4959  Description of women's death risk warning at b...  
4960  Fabio Capello: After Coronavirus La Liga Only ...  
4961         Jet response from TFF!'' They Target Us ''  
4962  Mask was distributed in Ahimehmet and Yeşiltep...  
4963  Prosecutor's Carsitaki Judge Yarsu has been mo...  

[4964 rows x 9 columns]

In [17]:
path = 'train/_TRAIN_title_translated.csv'
title_df.to_csv(path,index=False)  



### Embedding and cosine similarity

A pre-trained model (BERT) is used to embed the translated titles. The documentation of the used language model can be found at [SentenceTransformer](https://www.sbert.net/docs/package_reference/SentenceTransformer.html). <br><br>

After that, cosine similarity is applied by using the SKLearn package. The documentation can be found at [Cosine Similarity](https://scikit-learn.org/stable/modules/generated/sklearn.metrics.pairwise.cosine_similarity.html).

In [20]:
title_cos_sim_df = pd.DataFrame(columns = ["pair_id","url1_lang", "google_lang1","url2_lang","google_lang2", "title1","title2","translated1","translated2","cos_sim"])

for i, row in title_df.iterrows():
    cos_sim = 0
    sentences = [
        str(row['translated1']),
        str(row['translated2']),
    ]

    sentence_embeddings = model.encode(sentences)

    cs = cosine_similarity(
        [sentence_embeddings[0]],
        sentence_embeddings[1:]
    )
    cos_sim = cs[0][0]
    
    print('--------------',i,'---------------')
    print(row['pair_id'])
    for s in sentences:
        print(s)
    print('cos_sim: ',cos_sim)
    
    pair = row['pair_id']
    entry = {"pair_id": pair,"url1_lang":row['url1_lang'],"google_lang1":row['google_lang1'],"url2_lang":row['url2_lang'],"google_lang2":row['google_lang2'],"title1":row["title1"],"title2":row["title2"],"translated1":row['translated1'],"translated2":row['translated2'],"cos_sim":cos_sim}
    title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)



-------------- 0 ---------------
1484084337_1484110209
Virginia man arrested in fatal DUI crash in West Virginia
Haiti’s leader marks independence day amid security concerns
cos_sim:  0.27247515
-------------- 1 ---------------
1484396422_1483924666
Guyana: Three injured after car crashes into utility pole
Fire kills more than 30 animals at zoo in western Germany
cos_sim:  0.5614324


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\2103379383.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\2103379383.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)


-------------- 2 ---------------
1484698254_1483758694
Trump Brings In 2020 At Mar-a-Lago: ‘We’re Going To Have A Great Year’
Trump says he does not expect war with Iran, ‘likes peace’
cos_sim:  0.44692904
-------------- 3 ---------------
1576314516_1576455088
Zomato Buys Uber’s Food Delivery Business in India
Indian Online Food Delivery Market to Hit $8 Billion by 2022: Google, BCG Report
cos_sim:  0.60913646


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\2103379383.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\2103379383.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)


-------------- 4 ---------------
1484036253_1483894099
India approves third moon mission, months after landing failure
India targets new moon mission in 2020
cos_sim:  0.6344524
-------------- 5 ---------------
1484189120_1484113136
Wiesenthal Center Calls for FBI Task Force to Deal with Anti-Semitism
Jewish Groups React to Monsey Stabbings
cos_sim:  0.52070516


...

C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\2103379383.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\2103379383.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)


-------------- 4960 ---------------
1590915424_1590940388
Survival Struggle in La Liga Clubs due to Kovid-19
Fabio Capello: After Coronavirus La Liga Only Real Madrid will be standing
cos_sim:  0.55748594
-------------- 4961 ---------------
1526157103_1492737005
The palace has not been the remedy: 'Giant Clubs in the Boror Drinking Desk'
Jet response from TFF!'' They Target Us ''
cos_sim:  0.27167547


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\2103379383.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\2103379383.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)


-------------- 4962 ---------------
1603274500_1618292937
Ergene Municipality continues to disrupt road work
Mask was distributed in Ahimehmet and Yeşiltepe neighborhoods in Ergene
cos_sim:  0.382091
-------------- 4963 ---------------
1597247537_1604202164
The group had launched members of the comment members ... Ibrahim Gökçek left the death of death!
Prosecutor's Carsitaki Judge Yarsu has been moving due to shares on DHKP-C defendant
cos_sim:  0.5224623


C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\2103379383.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)
C:\Users\Potsdam\AppData\Local\Temp\ipykernel_25748\2103379383.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  title_cos_sim_df = title_cos_sim_df.append(entry, ignore_index = True)


In [21]:
title_cos_sim_df

pair_id url1_lang google_lang1 url2_lang google_lang2  \
0     1484084337_1484110209        en           en        en           en   
1     1484396422_1483924666        en           en        en           en   
2     1484698254_1483758694        en           en        en           en   
3     1576314516_1576455088        en           en        en           en   
4     1484036253_1483894099        en           en        en           en   
...                     ...       ...          ...       ...          ...   
4959  1586195445_1598778991        tr           tr        tr           tr   
4960  1590915424_1590940388        tr           tr        tr           tr   
4961  1526157103_1492737005        tr           tr        tr           tr   
4962  1603274500_1618292937        tr           tr        tr           tr   
4963  1597247537_1604202164        tr           tr        tr           tr   

                                                 title1  \
0     Virginia man arrested in fatal DUI crash in We...   
1     Guyana: Three injured after car crashes into u...   
2     Trump Brings In 2020 At Mar-a-Lago: ‘We’re Goi...   
3     Zomato Buys Uber’s Food Delivery Business in I...   
4     India approves third moon mission, months afte...   
...                                                 ...   
4959  BM, Aden'de 2 bini aşkın iç göçmenin selden za...   
4960  Kovid-19'dan dolayı La Liga kulüplerinde hayat...   
4961  Saray da çare olmadı: 'Borca boğulan dev kulüp...   
4962  Ergene Belediyesi yol çalışmalarına aksatmadan...   
4963  Grup Yorum üyeleri zorla başlatmıştı... İbrahi...   

                                                 title2  \
0     Haiti’s leader marks independence day amid sec...   
1     Fire kills more than 30 animals at zoo in west...   
2     Trump says he does not expect war with Iran, ‘...   
3     Indian Online Food Delivery Market to Hit $8 B...   
4                India targets new moon mission in 2020   
...                                                 ...   
4959  BM'den Yemen'de kadınların doğumda ölüm riski ...   
4960  Fabio Capello: Koronavirüs sonrası La Liga'da ...   
4961    TFF’den jet yanıt! ''Bizi hedef gösteriyorlar''   
4962  Ergene'de Ahimehmet ve Yeşiltepe mahallelerind...   
4963  Savcılık Karşıyaka Hakimi Sarısu'nun DHKP-C sa...   

                                            translated1  \
0     Virginia man arrested in fatal DUI crash in We...   
1     Guyana: Three injured after car crashes into u...   
2     Trump Brings In 2020 At Mar-a-Lago: ‘We’re Goi...   
3     Zomato Buys Uber’s Food Delivery Business in I...   
4     India approves third moon mission, months afte...   
...                                                 ...   
4959  UN explained that over 2,000 domestic migrants...   
4960  Survival Struggle in La Liga Clubs due to Kovi...   
4961  The palace has not been the remedy: 'Giant Clu...   
4962  Ergene Municipality continues to disrupt road ...   
4963  The group had launched members of the comment ...   

                                            translated2   cos_sim  
0     Haiti’s leader marks independence day amid sec...  0.272475  
1     Fire kills more than 30 animals at zoo in west...  0.561432  
2     Trump says he does not expect war with Iran, ‘...  0.446929  
3     Indian Online Food Delivery Market to Hit $8 B...  0.609136  
4                India targets new moon mission in 2020  0.634452  
...                                                 ...       ...  
4959  Description of women's death risk warning at b...  0.549759  
4960  Fabio Capello: After Coronavirus La Liga Only ...  0.557486  
4961         Jet response from TFF!'' They Target Us ''  0.271675  
4962  Mask was distributed in Ahimehmet and Yeşiltep...  0.382091  
4963  Prosecutor's Carsitaki Judge Yarsu has been mo...  0.522462  

[4964 rows x 10 columns]

In [61]:
path = 'train/_TRAIN_title_cosSim_score.csv'
title_cos_sim_df.to_csv(path,index=False)